# LiteRT ModelUtils Get Started
Last Updated: 04/11/2025

LiteRT ModelUtils is the Python toolkit for creating, inspecting, and rewriting TFLite/LiteRT flatbuffer models. ModelUtils is built using powerful tools like the ODML Converter and the TFLite MLIR backend, ensuring it's reliable and packed with features. Plus, it's designed to work seamlessly with C++ MLIR, making it easy to integrate into other MLIR-based workflows.

This notebook requires local colab runtime. Please use the following command to start the runtime:
```bash
blaze run -c opt //litert/python/tools/model_utils:colab

```


## Prepare a Sample LiteRT Model

This section will create a simple `.tflite` model and save it to `/tmp/test.tflite`. We'll use this model to demonstrate the features and APIs of ModelUtils. The model will perform basic operations like addition, subtraction, multiplication, a fully-connected layer, and ReLU activation.



In [1]:
import torch
import ai_edge_torch

class SampleModel(torch.nn.Module):
  def __init__(self):
    super().__init__()
    self.w1 = torch.randn(10, 10)
    self.fc = torch.nn.Linear(10, 20)
    self.w2 = torch.randn(10, 20)
    self.relu = torch.nn.ReLU()

  def forward(self, x, y):
    x = x + self.w1
    x = x - y
    x = self.fc(x)
    x = x * self.w2
    x = self.relu(x)
    return x

model = SampleModel().eval()
args = (torch.randn(10, 10), torch.randn(10, 10))
em = ai_edge_torch.convert(model, args)
em.export("/tmp/test.tflite")

/usr/local/google/_blaze_cnchan/f4b7afe819e84ba50137d18ac992985a/execroot/google3/blaze-out/k8-opt/bin/litert/python/tools/model_utils/colab.runfiles/google3/third_party/py/torch/distributed/distributed_c10d.py:355: UserWarning: Device capability of jax unspecified, assuming `cpu` and `cuda`. Please specify it via the `devices` argument of `register_backend`.
  warnings.warn(
/usr/local/google/_blaze_cnchan/f4b7afe819e84ba50137d18ac992985a/execroot/google3/blaze-out/k8-opt/bin/litert/python/tools/model_utils/colab.runfiles/google3/third_party/py/torch/export/_unlift.py:81: UserWarning: Attempted to insert a get_attr Node with no underlying reference in the owning GraphModule! Call GraphModule.add_submodule to add the necessary submodule, GraphModule.add_parameter to add the necessary Parameter, or nn.Module.register_buffer to add the necessary buffer
  getattr_node = gm.graph.get_attr(lifted_node)
/usr/local/google/_blaze_cnchan/f4b7afe819e84ba50137d18ac992985a/execroot/google3/blaze-o

## Read LiteRT Flatbuffer Model

Now, let's use ModelUtils to load the `.tflite` model we just created. The `mu.read_flatbuffer()` function reads the model from the file and returns an ModelUtils `ModuleOp`.

In [2]:
from google3.third_party.odml.litert.litert.python.tools import model_utils as mu

# Load the TFLite model from the file path we specified earlier.
# This function returns two values:
#   - module: The ModuleOp representation of the model.
#   - ir_ctx: The MLIR context associated with the module (this will be used later when editing the module).
module, ir_ctx = mu.read_flatbuffer("/tmp/test.tflite")

print(module)

builtin.module {tf_saved_model.semantics = ##unit, tfl.description = #string"MLIR Converted.", tfl.metadata = ##{CONVERSION_METADATA = "\10\00\00\00\00\00\00\00\08\00\0E\00\08\00\04\00\08\00\00\00\10\00\00\00$\00\00\00\00\00\06\00\08\00\04\00\06\00\00\00\04\00\00\00\00\00\00\00\0C\00\18\00\14\00\10\00\0C\00\04\..., tfl.schema_version = #int3 : i32} {
  "func.func"() ({
  ^0(%0 : !tensor<10x10xf32>, %1 : !tensor<10x10xf32>):
    %2 = "arith.constant"() {value = #dense[-0.04109585, -1.5635458 , -0.81136984, ...,  0.24584153,  0.04777608, -0.7674694 ]} : () -> !tensor<10x10xf32>
    %3 = "tfl.add"(%0, %2) {fused_activation_function = #string"NONE"} : (!tensor<10x10xf32>, !tensor<10x10xf32>) -> !tensor<10x10xf32>
    %4 = "tfl.sub"(%3, %1) {fused_activation_function = #string"NONE"} : (!tensor<10x10xf32>, !tensor<10x10xf32>) -> !tensor<10x10xf32>
    %5 = "arith.constant"() {value = #dense[-0.23799081,  0.19839475, -0.05831808, ..., -0.25562975,  0.31411973, -0.1036488 ]} : () -> !tensor<2

To inspect the operations within the "main" function, we first retrieve the function operation (`func.FuncOp`) from the module. Each function has a symbolic name, accessible via `FuncOp.sym_name`. We use this to find the "main" function (which is the default name when signature name is unspecified). We could iterate through the operations within this function using `FuncOp.ops` to print and inspect each operation.

In [3]:
# Retrieve the "main" function operation (func.FuncOp) using its symbolic name.
main_func = next(op for op in module.ops if op.sym_name == "main")

for i, op in enumerate(main_func.ops):
  print(f"{i}-th op:", op)

0-th op: %0 = "arith.constant"() {value = #dense[-0.04109585, -1.5635458 , -0.81136984, ...,  0.24584153,  0.04777608, -0.7674694 ]} : () -> !tensor<10x10xf32>
1-th op: %0 = "tfl.add"(%1, %2) {fused_activation_function = #string"NONE"} : (!tensor<10x10xf32>, !tensor<10x10xf32>) -> !tensor<10x10xf32>
2-th op: %0 = "tfl.sub"(%1, %2) {fused_activation_function = #string"NONE"} : (!tensor<10x10xf32>, !tensor<10x10xf32>) -> !tensor<10x10xf32>
3-th op: %0 = "arith.constant"() {value = #dense[-0.23799081,  0.19839475, -0.05831808, ..., -0.25562975,  0.31411973, -0.1036488 ]} : () -> !tensor<20x10xf32>
4-th op: %0 = "arith.constant"() {value = #dense[-0.07478777,  0.04125437,  0.1914095 , ...,  0.18029064, -0.2845971 , -0.07858098]} : () -> !tensor<20xf32>
5-th op: %0 = "tfl.fully_connected"(%1, %2, %3) {asymmetric_quantize_inputs = #boolfalse, fused_activation_function = #string"NONE", keep_num_dims = #booltrue, weights_format = #string"DEFAULT"} : (!tensor<10x10xf32>, !tensor<20x10xf32>, !te

### Operations APIs

Now, let's try to get the `tfl.fully_connected` op from the main func:

In [4]:
for op in main_func.ops:
  if op.name == "tfl.fully_connected":
    fc_op = op
    break

print(fc_op)

%0 = "tfl.fully_connected"(%1, %2, %3) {asymmetric_quantize_inputs = #boolfalse, fused_activation_function = #string"NONE", keep_num_dims = #booltrue, weights_format = #string"DEFAULT"} : (!tensor<10x10xf32>, !tensor<20x10xf32>, !tensor<20xf32>) -> !tensor<10x20xf32>


#### Operands
We can access the inputs of the `tfl.fully_connected` operation using its `operands` property. The `operands` property is a list of `SSAValue` objects, each representing an input value or edge in the computation graph. These SSA values can be the result of a previous operation or an argument to the function. To find the operation that *produces* a given `SSAValue` (i.e., the source of the input), we use the `SSAValue.owner` property.

If the `SSAValue` is a function argument (not the result of an operation), `owner` will be `None`. In our example below we extract the input, weight and bias of the fully connected op. Then we get the owner of the input which is a `tfl.sub` op.

In [5]:
print("Number of operands:", len(fc_op.operands))

# Access the operands (inputs) of the fully connected operation.
# fc_op.operands is a list of SSAValue objects.
input, weight, bias = fc_op.operands

# Print each operand (input, weight, bias).
print("Input:", input)
print("Weight:", weight)
print("Bias:", bias)

# Get the operation that *produces* the input SSAValue.
# SSAValue.owner returns the Op that generates the value, or None if it's a function argument.
sub_op = input.owner
print("=====")
print(sub_op)

Number of operands: 3
Input: <OpResult[!tensor<10x10xf32>] index: 0, operation: tfl.sub, uses: 1>
Weight: <OpResult[!tensor<20x10xf32>] index: 0, operation: arith.constant, uses: 1>
Bias: <OpResult[!tensor<20xf32>] index: 0, operation: arith.constant, uses: 1>
=====
%0 = "tfl.sub"(%1, %2) {fused_activation_function = #string"NONE"} : (!tensor<10x10xf32>, !tensor<10x10xf32>) -> !tensor<10x10xf32>


The type information is available in `SSAValue.type`. For most of the `tfl.` operations, the inputs and outputs `SSAValue` are in `mlir.RankedTesnorType`, where you can get the shape and dtype from the type:

In [6]:
input, weight, bias = fc_op.operands

print("Input type:", input.type)
print("Input dtype:", input.type.element_type)
print("Input shape:", input.type.shape)

Input type: !tensor<10x10xf32>
Input dtype: f32
Input shape: [10, 10]


#### Results

Similar to how we accessed inputs using `operands`, we can access the outputs of an operation using its `results` property. The `results` property is a list of `OpResult` objects, representing the values produced by the operation. Each `OpResult` can be used as an input (`SSAValue`) to other operations. To find where a given `OpResult` is used, we can iterate through its `uses` property. Each element in `uses` is a `Use` object which contains information about how the `OpResult` is used. The `Use.operation` property gives us the operation that uses this `OpResult` as an input. In this example, we show that the output of the `tfl.fully_connected` operation is used by the `tfl.mul` operation.

In [7]:
print("Number of results:", len(fc_op.results))

# Access the results (outputs) of the fully connected operation.
# fc_op.results is a list of OpResult objects.
output = fc_op.results[0]
print("Output:", output)

# Iterate through the uses of the output OpResult.
# output.uses is a list of Use objects, indicating where the output is used.
print("===")
for use in output.uses:
  print(use)
  child_op = use.operation
  print(child_op)

Number of results: 1
Output: <OpResult[!tensor<10x20xf32>] index: 0, operation: tfl.fully_connected, uses: 1>
===
Use(operation=MulOp(_operands=(<OpResult[!tensor<10x20xf32>] index: 0, operation: tfl.fully_connected, uses: 1>, <OpResult[!tensor<10x20xf32>] index: 0, operation: arith.constant, uses: 1>), results=(<OpResult[!tensor<10x20xf32>] index: 0, operation: tfl.mul, uses: 1>,), _successors=(), properties={}, attributes={'fused_activation_function': StringAttr(data='RELU')}, regions=()), index=0)
%0 = "tfl.mul"(%1, %2) {fused_activation_function = #string"RELU"} : (!tensor<10x20xf32>, !tensor<10x20xf32>) -> !tensor<10x20xf32>


#### Attributes

You can access an operation's attributes in two ways:

1. Through the `op.attributes` dictionary
2. Directly using `op.<attribute_name>`.

The items in the `op.attributes` dictionary are `mu.core.MlirAttributeBase` objects, which are MLIR's representation of attributes. Accessing attributes via `op.<attribute_name>` provides a convenient shortcut, allowing you to get or set attribute values as plain Python objects (like strings, integers, or booleans). This shortcut automatically handles the conversion between Python objects and the underlying `MlirAttributeBase` objects.

In [8]:
# op.attributes is a dictionary where keys are attribute names (strings) and values are MlirAttributeBase objects.
print(op.attributes)

# Access an attribute through the attributes dictionary.
# The value retrieved is a MlirAttributeBase object.
print(op.attributes["fused_activation_function"], type(op.attributes["fused_activation_function"]))

# Access an attribute directly using op.<attribute_name>.
# This provides a shortcut to access the attribute value as a plain Python object.
print(op.fused_activation_function, type(op.fused_activation_function))

{'asymmetric_quantize_inputs': BoolAttr(data=False), 'fused_activation_function': StringAttr(data='NONE'), 'keep_num_dims': BoolAttr(data=True), 'weights_format': StringAttr(data='DEFAULT')}
#string"NONE" <class 'google3.third_party.odml.litert.litert.python.tools.model_utils.dialect.mlir.StringAttr'>
NONE <class 'str'>


### Constant in Numpy

You can get the tensor value in from a constant op with `const_op.numpy()`.

In [9]:
input, bias, weight = fc_op.operands

bias = bias.owner.numpy()
print(type(bias), bias.shape, bias.dtype)

<class 'numpy.ndarray'> (20, 10) float32


## Edit LiteRT Flatbuffer Model

In [10]:
import copy
original_module, ir_ctx = mu.read_flatbuffer("/tmp/test.tflite")

#### Update Op Attributes

To make changes to the MLIR representation, we need to work within the `ir_ctx` context manager, required by the underlying MLIR backend.

In the code below, we iterate through the operations in the main function and modify the `fused_activation_function` attribute of the `tfl.fully_connected operation` to "NONE". This effectively removes the fused activation function (RELU in the example) from the operation.

In [11]:
module = copy.deepcopy(original_module)

with ir_ctx:
  for op in module.walk():
    if op.name == "tfl.fully_connected":
      op.fused_activation_function = "NONE"
  module.cleanup()
  print(module)

builtin.module {tf_saved_model.semantics = ##unit, tfl.description = #string"MLIR Converted.", tfl.metadata = ##{CONVERSION_METADATA = "\10\00\00\00\00\00\00\00\08\00\0E\00\08\00\04\00\08\00\00\00\10\00\00\00$\00\00\00\00\00\06\00\08\00\04\00\06\00\00\00\04\00\00\00\00\00\00\00\0C\00\18\00\14\00\10\00\0C\00\04\..., tfl.schema_version = #int3 : i32} {
  "func.func"() ({
  ^0(%0 : !tensor<10x10xf32>, %1 : !tensor<10x10xf32>):
    %2 = "arith.constant"() {value = #dense[-0.7441374 , -1.7072843 , -0.70359725, ..., -0.39670816, -0.8744835 , -0.777736  ]} : () -> !tensor<10x20xf32>
    %3 = "arith.constant"() {value = #dense[-0.07478777,  0.04125437,  0.1914095 , ...,  0.18029064, -0.2845971 , -0.07858098]} : () -> !tensor<20xf32>
    %4 = "arith.constant"() {value = #dense[-0.23799081,  0.19839475, -0.05831808, ..., -0.25562975,  0.31411973, -0.1036488 ]} : () -> !tensor<20x10xf32>
    %5 = "arith.constant"() {value = #dense[-0.04109585, -1.5635458 , -0.81136984, ...,  0.24584153,  0.047776

#### Remove Op(s)

ModelUtils allows you to remove operations from the model. However, instead of directly erasing them, we achieve this by "rewiring" the computation graph. The basic idea is to redirect the uses of the deleted operation's output to another suitable input.

Here, we demonstrate removing all tfl.sub operations:

In [12]:
# Create a deep copy of the original module to avoid modifying it directly.
module = copy.deepcopy(original_module)

with ir_ctx:
  # Iterate through all operations in the module and rewire uses of tfl.sub.
  for op in module.walk():
    if op.name == "tfl.sub":
      input = op.operands[0]
      output = op.results[0]
      assert input.type.shape == output.type.shape
      for use in list(output.uses):  # Iterate through a copy to avoid modification errors
        use.operation.operands[use.index] = input

  # Perform final cleanup after rewiring.
  module.cleanup()

  # Print the modified of the whole module.
  print(module)

builtin.module {tf_saved_model.semantics = ##unit, tfl.description = #string"MLIR Converted.", tfl.metadata = ##{CONVERSION_METADATA = "\10\00\00\00\00\00\00\00\08\00\0E\00\08\00\04\00\08\00\00\00\10\00\00\00$\00\00\00\00\00\06\00\08\00\04\00\06\00\00\00\04\00\00\00\00\00\00\00\0C\00\18\00\14\00\10\00\0C\00\04\..., tfl.schema_version = #int3 : i32} {
  "func.func"() ({
  ^0(%0 : !tensor<10x10xf32>, %1 : !tensor<10x10xf32>):
    %2 = "arith.constant"() {value = #dense[-0.7441374 , -1.7072843 , -0.70359725, ..., -0.39670816, -0.8744835 , -0.777736  ]} : () -> !tensor<10x20xf32>
    %3 = "arith.constant"() {value = #dense[-0.07478777,  0.04125437,  0.1914095 , ...,  0.18029064, -0.2845971 , -0.07858098]} : () -> !tensor<20xf32>
    %4 = "arith.constant"() {value = #dense[-0.23799081,  0.19839475, -0.05831808, ..., -0.25562975,  0.31411973, -0.1036488 ]} : () -> !tensor<20x10xf32>
    %5 = "arith.constant"() {value = #dense[-0.04109585, -1.5635458 , -0.81136984, ...,  0.24584153,  0.047776

### Create New Op

In [13]:
import numpy as np
from google3.third_party.odml.litert.litert.python.tools.model_utils.dialect import mlir
from google3.third_party.odml.litert.litert.python.tools.model_utils.dialect import tfl

# Create a deep copy of the original module to avoid modifying it directly.
module = copy.deepcopy(original_module)

with ir_ctx:
  for op in module.walk():
    if op.name == "tfl.sub":
      # Extract operands and output.
      lhs, rhs = op.operands
      output = op.results[0]

      # Create OpBuildingContext for creating new ops within the module.
      with mu.OpBuildingContext(anchor=op):
        # Negate RHS using constant multiplication.
        neg_one_const = tfl.const(np.array([-1.0], dtype=np.float32))
        neg_rhs = tfl.mul(rhs, neg_one_const)

        # Perform element-wise negation using addition with negated RHS.
        new_output = tfl.add(lhs, neg_rhs)

        # Replace the original output with the result of the new computation.
        output.replace_by(new_output)

  # Perform final cleanup after modifications.
  module.cleanup()

  # Print the modified MLIR representation of the whole module.
  print(module)

builtin.module {tf_saved_model.semantics = ##unit, tfl.description = #string"MLIR Converted.", tfl.metadata = ##{CONVERSION_METADATA = "\10\00\00\00\00\00\00\00\08\00\0E\00\08\00\04\00\08\00\00\00\10\00\00\00$\00\00\00\00\00\06\00\08\00\04\00\06\00\00\00\04\00\00\00\00\00\00\00\0C\00\18\00\14\00\10\00\0C\00\04\..., tfl.schema_version = #int3 : i32} {
  "func.func"() ({
  ^0(%0 : !tensor<10x10xf32>, %1 : !tensor<10x10xf32>):
    %2 = "arith.constant"() {value = #dense[-0.7441374 , -1.7072843 , -0.70359725, ..., -0.39670816, -0.8744835 , -0.777736  ]} : () -> !tensor<10x20xf32>
    %3 = "arith.constant"() {value = #dense[-0.07478777,  0.04125437,  0.1914095 , ...,  0.18029064, -0.2845971 , -0.07858098]} : () -> !tensor<20xf32>
    %4 = "arith.constant"() {value = #dense[-0.23799081,  0.19839475, -0.05831808, ..., -0.25562975,  0.31411973, -0.1036488 ]} : () -> !tensor<20x10xf32>
    %5 = "arith.constant"() {value = #dense[-1.]} : () -> !tensor<1xf32>
    %6 = "arith.constant"() {value = 

### ModelUtils Match-and-Rewrite Pass

In [14]:
from google3.third_party.odml.litert.litert.python.tools.model_utils.dialect import mlir
from google3.third_party.odml.litert.litert.python.tools.model_utils.dialect import tfl
import numpy as np

class MyPass(mu.core.RewritePatternPassBase):
  name = "my-pass"

@MyPass.register_rewrite_pattern(tfl.SubOp)
def sub_to_add(op: tfl.SubOp, rewriter):
  with mu.MatchingContext():
    # mu.match.pred under mu.MatchingContext is a shortcut for:
    # `if not ....: return`
    mu.match.pred(op.name == "tfl.sub")
    mu.match.pred(op.fused_activation_function == "NONE")

    output = op.results[0]
    mu.match.pred(output.type.shape[0] == 10)

    print("Rewriting", op, "...")

    lhs, rhs = op.operands
    with mu.OpBuildingContext(anchor=rewriter):
      # Negate RHS using constant multiplication.
      neg_one_const = tfl.const(np.array([-1.0], dtype=np.float32))
      neg_rhs = tfl.mul(rhs, neg_one_const)

      # Perform element-wise negation using addition with negated RHS.
      new_output = tfl.add(lhs, neg_rhs)

      # Replace the original output with the result of the new computation.
      output.replace_by(new_output)

      # Erase the matched op to avoid recursive matching
      rewriter.erase_op(op)

module = copy.deepcopy(original_module)
with ir_ctx:
  MyPass()(module)

  module.cleanup()
  print(module)

Rewriting %0 = "tfl.sub"(%1, %2) {fused_activation_function = #string"NONE"} : (!tensor<10x10xf32>, !tensor<10x10xf32>) -> !tensor<10x10xf32> ...
builtin.module {tf_saved_model.semantics = ##unit, tfl.description = #string"MLIR Converted.", tfl.metadata = ##{CONVERSION_METADATA = "\10\00\00\00\00\00\00\00\08\00\0E\00\08\00\04\00\08\00\00\00\10\00\00\00$\00\00\00\00\00\06\00\08\00\04\00\06\00\00\00\04\00\00\00\00\00\00\00\0C\00\18\00\14\00\10\00\0C\00\04\..., tfl.schema_version = #int3 : i32} {
  "func.func"() ({
  ^0(%0 : !tensor<10x10xf32>, %1 : !tensor<10x10xf32>):
    %2 = "arith.constant"() {value = #dense[-0.7441374 , -1.7072843 , -0.70359725, ..., -0.39670816, -0.8744835 , -0.777736  ]} : () -> !tensor<10x20xf32>
    %3 = "arith.constant"() {value = #dense[-0.07478777,  0.04125437,  0.1914095 , ...,  0.18029064, -0.2845971 , -0.07858098]} : () -> !tensor<20xf32>
    %4 = "arith.constant"() {value = #dense[-0.23799081,  0.19839475, -0.05831808, ..., -0.25562975,  0.31411973, -0.10

#### TableGen DAG Matcher

ModelUtils provides matcher to match a DAG with llvm TableGen syntax. This is an efficient way to match a subgraph with more than one ops.

The following is an example for subgraph matching with DAG:

In [15]:
from google3.third_party.odml.litert.litert.python.tools.model_utils.dialect import mlir
from google3.third_party.odml.litert.litert.python.tools.model_utils.dialect import tfl
import numpy as np

class MyPass(mu.core.RewritePatternPassBase):
  name = "my-pass"

@MyPass.register_rewrite_pattern(tfl.SubOp)
def add_sub_to_mul(op: tfl.SubOp, rewriter):
  with mu.MatchingContext():

    _ = mu.match.dag("""
      (TFL_SubOp:$sub
        (TFL_AddOp:$add $lhs, TFL_ConstantOp:$cst),
        $rhs
      )
    """, op)
    print("Rewriting...")
    with mu.OpBuildingContext(rewriter):
      x = tfl.mul(_.lhs, _.rhs)
      _.sub.replace_by(x)

      rewriter.erase_op(op)

module = copy.deepcopy(original_module)
with ir_ctx:
  module.cleanup()
  print("Original Module:")
  print(module)

  print("================")
  MyPass()(module)
  module.cleanup()

  print("Modified Module:")
  print(module)

Original Module:
builtin.module {tf_saved_model.semantics = ##unit, tfl.description = #string"MLIR Converted.", tfl.metadata = ##{CONVERSION_METADATA = "\10\00\00\00\00\00\00\00\08\00\0E\00\08\00\04\00\08\00\00\00\10\00\00\00$\00\00\00\00\00\06\00\08\00\04\00\06\00\00\00\04\00\00\00\00\00\00\00\0C\00\18\00\14\00\10\00\0C\00\04\..., tfl.schema_version = #int3 : i32} {
  "func.func"() ({
  ^0(%0 : !tensor<10x10xf32>, %1 : !tensor<10x10xf32>):
    %2 = "arith.constant"() {value = #dense[-0.7441374 , -1.7072843 , -0.70359725, ..., -0.39670816, -0.8744835 , -0.777736  ]} : () -> !tensor<10x20xf32>
    %3 = "arith.constant"() {value = #dense[-0.07478777,  0.04125437,  0.1914095 , ...,  0.18029064, -0.2845971 , -0.07858098]} : () -> !tensor<20xf32>
    %4 = "arith.constant"() {value = #dense[-0.23799081,  0.19839475, -0.05831808, ..., -0.25562975,  0.31411973, -0.1036488 ]} : () -> !tensor<20x10xf32>
    %5 = "arith.constant"() {value = #dense[-0.04109585, -1.5635458 , -0.81136984, ...,  0.24

### Save Edited Module

In [16]:
with ir_ctx:
  mu.write_flatbuffer(module, "/tmp/updated.tflite")

## Model Explorer Visualization

`mu.visualize` is the Model Explorer integration for visualizing ModelUtils objects.

In [17]:
module = copy.deepcopy(original_module)

for op in module.walk():
  if op.name == "tfl.fully_connected":
    # Open Model Explorer on module and zoom-in the first FC op
    mu.visualize(op)
    break

ℹ️ Please re-run the cell in each new session

Loading extensions...
Loaded 8 extensions:
 - TFLite adapter (Flatbuffer)
 - TFLite adapter (MLIR)
 - TF adapter (MLIR)
 - TF adapter (direct)
 - GraphDef adapter
 - Pytorch adapter (exported program)
 - MLIR adapter
 - JSON adapter


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# Examples

- **TFL Search Model**: The template for building a py-binary tool to find the minimal reproduce subgraph for flatbuffer consumer issues (culprit finder): [google3/experimental/users/cnchan/tfl_search_model/tfl_search_model.py](https://source.corp.google.com/piper///depot/google3/experimental/users/cnchan/tfl_search_model/tfl_search_model.py)
- **Post-Conversion Model Surgery**: TFLite post-conversion model editing passes for hardware/model specific optimizations/de-optimizations: [google3/experimental/users/cnchan/snapfusion_opt/snapfusion_opt.py](https://source.corp.google.com/piper///depot/google3/experimental/users/cnchan/snapfusion_opt/snapfusion_opt.py)
- **Model Minifier for Debuging**: A debugging pass to replace all constant tensors with zero tensors, to make the flatbuffer smaller: [google3/experimental/users/cnchan/juno_opt/debug_pass.py](https://source.corp.google.com/piper///depot/google3/experimental/users/cnchan/juno_opt/debug_pass.py)